##set up

In [ ]:
import os 
import geocoder
import folium
from folium import plugins
import pandas as pd
import numpy as np
from sklearn.preprocessing import normalize
import datetime
from google.colab import files

now = datetime.datetime.now()
curr_year = now.year

#url="https://raw.githubusercontent.com/julia-sand/private/main/Helsinki_alueittain_2019%20-%20Taulukko.tsv?token=ARUCQSKEEY5ODHPGQIAN6ZLAR2I7E"
#data = pd.read_csv(url,header =0,index_col = 0,sep = "\t",skip_blank_lines=True)

#url_2 = "https://raw.githubusercontent.com/julia-sand/private/main/pop%20data1.txt?token=ARUCQSI4HWODA64ZY6YSGGDAR2I7A"
#pop_data = pd.read_csv(url_2,header =0,index_col = 0,sep = "\t",skip_blank_lines=True)

df_1 = pd.DataFrame(data)
df_2 = pd.DataFrame(pop_data)

df = df_1.copy()
df_pop = df_2.copy()

cols = df.iloc[1].values

df.drop(labels = df.index[0:3,],axis=0,inplace=True,errors = "ignore")

df.columns = cols

In [ ]:
num = len(df.index)

#add the coordinates via geocoder

coordinates = [[0,0],
               [0, 0],
               [60.16,24.95],
               [60.17,24.96],
               [60.1553993784,24.9427295624],
               [60.15524,24.911714],
               [60.17416597, 24.920996316],
               [60.155999376, 24.868663192],
               [0,0],
               #[62.6292,29.7609],
               [60.1999992, 24.8999964],
               [60.192332564, 24.872329844],
               [60.224832434, 24.876496494],
               [60.21916579, 24.85749657],
               [60.249999, 24.8833298],
               [0,0],
               [60.183832598, 24.942829562],
               [60.18833258, 24.938996244],
               [60.18999924, 24.953996184],
               [60.1999992, 24.926162962],
               [60.2166658, 24.9833294],
               [0,0],
               [60.2325,24.9294],
               [60.249999, 24.916663],
               [60.249999, 24.9333296],
               [60.223499106, 24.9666628],
               [60.249999, 24.9499962],
               [0,0],
               [60.24791,24.98858],
               [60.250165666, 25.00583331],
               [60.2833322, 25.0333332],
               [60.271165582, 25.034749861],
               [60.25666564, 25.07333304],
               [0,0],
               [60.1833326, 25.0166666],
               [60.1999992, 25.0499998],
               [60.1749993, 25.05249979],
               [0,0],
               [60.2166658, 25.0999996],
               [60.22166578, 25.071999712],
               [60.2333324, 25.1333328],
               [60.205332512, 25.13916611],
               [0,0],
               [60.24944,25.18778]]

df["coordinates"] = coordinates

for i in range(len(df.columns)-1):
    #swap commas with dots 
    try:
        df.iloc[:,i] = df.iloc[:,i].str.translate(str.maketrans(',.', '.,'))
        df.iloc[:,i] = df.iloc[:,i].astype(float)
    except:
        pass

#add dist level
dist_level = np.zeros(len(df.index))
for i in range(len(df.index)):
    if "suur" in df.index[i]:
        dist_level[i] = 1
    elif "Helsinki" in df.index[i]:
        dist_level[i] = 2

df["dist_level"] = dist_level

#############GEOCODER############
#coords = []
#for i in range(num): 
#    location = df_all.District.iloc[i]
#    loc = geocoder.osm(location)     
#    row = [loc.lat,loc.lng]
#    coords.append(row)
#df["coords"] = coords

#add district id column 
dist_id = np.zeros(num)
for i in range(num):
    if len(df.index[i]) == 1:
        var = df.index[i]
    dist_id[i] = var

df["dist_id"] = dist_id

#format index
df.set_index(df.index.str.split(" +",expand = True),inplace=True)

df.reset_index(inplace=True)  

df.set_index("level_0",inplace=True)

#drop extra columns
df.drop(["level_1","level_2","level_3"], axis=1,inplace=True, errors="ignore")

#fix district names
df["District"] = ["Helsinki",
                  "Eteläinen",
                  "Vironniemi",
                  "Ullanlinna",
                  "Kampinmalmi",
                  "Taka-Töölö",
                  "Lauttasaari",
                  "Läntinen",
                  "Reijola",
                  "Munkkiniemi",
                  "Haaga",
                  "Pitäjänmäki",
                  "Kaarela",
                  "Keskinen",
                  "Kallio",
                  "Alppiharju",
                  "Vallila",
                  "Pasila",
                  "Vanhankaupunki",
                  "Pohjoinen",
                  "Maunula",
                  "Länsi-Pakila",
                  "Tuomarinkylä",
                  "Oulunkylä",
                  "Itä-Pakila",
                  "Koillinen",
                  "Latokartano",
                  "Pukinmäki",
                  "Malmi",
                  "Suutarila",
                  "Puistola",
                  "Jakomäki",
                  "Kaakkoinen",
                  "Kulosaari",
                  "Herttoniemi",
                  "Laajasalo",
                  "Itäinen",
                  "Vartiokylä",
                  "Myllypuro",
                  "Mellunkylä",
                  "Vuosaari",
                  "Östersundomin",
                  "Östersundomi"]

#format column names for population
dates = np.arange(1985,2034,1,dtype=int)

df_pop.columns = dates

#remove zeros from numbers and format as floats
for i in range(len(df_pop.columns)-1):
    try: 
        df_pop.iloc[:,i] = df_pop.iloc[:,i].str.replace(r'\xa0','')
        df_pop.iloc[:,i] = df_pop.iloc[:,i].astype(float)
    except:
        pass

#format index for population df for join
df_pop.set_index(df_pop.index.str.split(" +",expand = True),inplace=True)
df_pop.reset_index(inplace=True)  
df_pop.set_index("level_0",inplace=True)

#drop extra columns
df_pop.drop(["level_1","level_2","level_3"], axis=1,inplace=True, errors="ignore")

#merge the data frames
df_all = df.merge(df_pop,how="outer",left_index=True,right_index=True)

#columns as strings
df_all.columns = df_all.columns.astype("str")

#fill nans
df_all = df_all.fillna(0)

#only small districts
df_perispiiri = df_all[df_all.dist_level == 0.0]
num_1 = len(df_perispiiri.index)

df_perispiiri_pop = df_perispiiri.loc[:,"1985":]
num_years = len(df_perispiiri_pop.columns)

#normalise features
norm_weights = normalize(df_perispiiri_pop,"l2",axis = 0) *10

#separate coordinates
lon = np.zeros(num_1)
lat = np.zeros(num_1)
for i in range(num_1):
    lon[i] = df_perispiiri.coordinates.iloc[i][0]
    lat[i] = df_perispiiri.coordinates.iloc[i][1]

#heat_data = [np.c_[lat,lon,norm_weights[:,j]].tolist() for j in range(num_years)]

df_suuri = df_all[df_all.dist_level == 1.0]
df_suuri_pop = df_suuri.loc[:,"1985":]

##Bokeh Tests

In [ ]:
from bokeh.models import NumeralTickFormatter
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.palettes import Spectral8
from bokeh.embed import file_html
from bokeh.resources import CDN


#only for all levels
df_plotting = df_all[df_all.dist_level == 1.0]

output_notebook()

p = figure(plot_width=1000, plot_height=600)
p.title.text = 'Population projections'

for i,color in zip(range(len(df_plotting.index)), Spectral8):
    #edit for [i,:] when re-running
    p.line(dates, df_pop.iloc[i,:], line_width=2, color = color, alpha=0.8, legend_label=df_plotting.District[i])

p.legend.location = "top_left"
p.legend.click_policy="hide"

p.yaxis.axis_label = 'Population'
p.xaxis.axis_label = 'Year'

html = file_html(p, CDN, "my plot")

#show in notebook 

#show(p)

In [ ]:
#only for all levels
#df_plotting = df_all[df_all.dist_level == 1.0]

output_notebook()

p = figure(plot_width=1000, plot_height=600)
p.title.text = 'Population projections'

for i,color in zip(range(len(df_plotting.index)), Spectral8):
    #edit for [i,:] when re-running
    p.line(dates, df_perispiiri_pop.iloc[i,:], line_width=2, color = color, alpha=0.8, legend_label=df_perispiiri.District[i])

p.legend.location = "top_left"
p.legend.click_policy="hide"

p.yaxis.axis_label = 'Population'
p.xaxis.axis_label = 'Year'

#show in notebook 

show(p)

In [ ]:
#get the html 
import json
from bokeh.resources import CDN
from bokeh.embed import file_html
from bokeh.io import output_file,save

output_file("test1.html")
save(p)

#files.download("test1.html")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

##Map Experimentation

In [ ]:

map = folium.Map(location=[60.20, 25.01],
                 tiles ="openstreetmap", 
                 zoom_start=11)

clusters = plugins.MarkerCluster(overlay=True, 
                         control=True, 
                         name = "Districts").add_to(map)

pop_radius = folium.FeatureGroup(name='Population Radius', 
                        overlay = True,
                        show=False, 
                        control = True)

full_pop = np.sum(df_perispiiri["2021"])

for i in range(num_1):
    
    radius = norm_weights[0,i] * 100
    #radius = 1000* df_perispiiri["2021"].iloc[i] / full_pop

    if radius > 50:
        color = "orange"
    else:
        color = "green"

    folium.CircleMarker(location=df_perispiiri.coordinates.iloc[i],
                        radius = radius,
                        color=color,
                        fill = False,
                        ).add_to(pop_radius)

for i in range(num_1):
    dat1 = "The number of churches in this district is" + str(df_perispiiri.Kirkko.iloc[i])

    iframe = folium.IFrame(html=dat1, width=200, height=60)
    popup = folium.Popup(iframe, max_width=2650)
    
    folium.Marker(
        location=df_perispiiri.coordinates.iloc[i], # coordinates for the marker
        popup=popup, # pop-up label- add full visualisation here?
        icon=folium.Icon(color = color),
        #add place name as tool tip on hover
        tooltip = df_perispiiri.District.iloc[i],
    ).add_to(clusters)

map.add_child(pop_radius)

colormap = {0.0: 'white', 0.1: 'blue', 0.3: 'green',  0.5: 'yellow', 0.6: 'red'}

#add weights
plugins.HeatMap(df_perispiiri.coordinates.values,
                        radius=radius,
                        min_opacity = 0.5,
                        #max_val=1.0,
                        #use_local_extrema=False,
                        #gradient=colormap,
                        control = True,
                        overlay=True,
                        name = "Population Heat Map",
                        show=False).add_to(map)

folium.LayerControl(position="topright",
                    autoZIndex = True, 
                    collapsed = False).add_to(map)


plugins.Fullscreen(position="topright",
                    title="Full Screen",
                    title_cancel="Exit Full Screen",
                    force_separate_button=True,
                ).add_to(map)



In [ ]:
#add an image - maybe logo of cityy?? 

from folium.plugins import FloatImage
url = ('https://www.hel.fi/wps/wcm/connect/b3717cdb-45a7-4575-946b-5ea799506c80/1/HELSINKI_Tunnus_MUSTA.png?MOD=AJPERES')
FloatImage(url, bottom=5, left=85).add_to(map)


##Heat Map With Time

In [ ]:
n = folium.Map(location=[60.20, 25.01],tiles ="Stamen Terrain", zoom_start=10.3)
colormap = {0.0: 'pink', 0.3: 'blue', 0.5: 'green',  0.7: 'yellow', 1.0: 'red'}

heat_vals = [np.c_[df_perispiiri.coordinates.values,norm_weights[:,i]] for i in norm_weights.shape[1]]
plugins.HeatMapWithTime(heat_vals,
                        radius=25,
                        min_opacity = 0.5,
                        max_opacity=1.0,
                        use_local_extrema=False,
                        gradient=colormap,
                        show=True).add_to(n)

##Population Spirals


In [ ]:
map_1 = folium.Map(location=[60.20, 25.01],
                 tiles =None, 
                 zoom_start=11,
                 min_zoom = 4,
                 max_zoom = 15,
                 max_bounds= True)

tile = folium.TileLayer('openstreetmap', name='my tilelayer',control=False)
tile.add_to(map_1)

#function to edit marker cluster appearance
icon_create_function = '''
     function(cluster) {
     var childCount = Math.round(cluster.getChildCount() / 50);
     return L.divIcon({html: '<div><span>' + childCount + '</div></span>' ,
                       className: 'marker-cluster marker-cluster-medium',
                       iconSize: new L.Point(30, 30)});
     }
 '''

fg_dists = folium.FeatureGroup(name="Districts",control=True,overlay=True)
fg_dists.add_to(map_1)

#separate clusters
clusters_south = plugins.MarkerCluster(overlay=True, 
                                control=True, 
                                #formatting for clusters
                                icon_create_function = icon_create_function,
                                name = "Eteläinen")
clusters_south.add_to(map_1)


clusters_west = plugins.MarkerCluster(overlay=True, 
                                control=True, 
                                show = False,
                                icon_create_function = icon_create_function,                                
                                name = "Läntinen").add_to(map_1)

clusters_center = plugins.MarkerCluster(overlay=True, 
                                show = False,
                                control=True, 
                                icon_create_function = icon_create_function,
                                name = "Keskinen").add_to(map_1)

clusters_north = plugins.MarkerCluster(overlay=True, 
                                control=True, 
                                show = False,
                                icon_create_function = icon_create_function,
                                name = "Pohjoinen").add_to(map_1)

clusters_koillinen = plugins.MarkerCluster(overlay=True, 
                                show = False,
                                control=True, 
                                icon_create_function = icon_create_function,
                                name = "Koillinen").add_to(map_1)

clusters_kaakkoinen = plugins.MarkerCluster(overlay=True,
                                show = False, 
                                icon_create_function = icon_create_function,
                                control=True, 
                                name = "Kaakkoinen").add_to(map_1)

clusters_east = plugins.MarkerCluster(overlay=True, 
                                icon_create_function = icon_create_function,
                                show = False,
                                control=True, 
                                name = "Itäinen").add_to(map_1)

clusters_oster = plugins.MarkerCluster(overlay=True, 
                                icon_create_function = icon_create_function,
                                show= False,
                                control=True, 
                                name = "Östersundomin").add_to(map_1)

#add markers for icons and pop-ups
for i in range(num_1):
    pop_loc = curr_year - 1985
    pop_curr = df_perispiiri_pop.iloc[i,pop_loc].astype(int)

    dat1 = "<b>The current population is </b>" + str(pop_curr)

    iframe = folium.IFrame(html=html, width=200, height=60)
    popup = folium.Popup(iframe, max_width=2650)
    
    markers = folium.Marker(
        location=df_perispiiri.coordinates.iloc[i], # coordinates for the marker
        popup=popup, # pop-up label- add full visualisation here?
        icon=folium.Icon(icon = "info-sign",
                         icon_color = "white"),
        #add place name as tool tip on hover
        tooltip = df_perispiiri.District.iloc[i],
        )
    
    if df_perispiiri.index[i] in ["101","102","103","104","105"]:
        markers.add_to(clusters_south)
    elif df_perispiiri.index[i] in ["201","202","203","204","205"]:
        markers.add_to(clusters_west)
    elif df_perispiiri.index[i] in ["301","302","303","304","305"]:
        markers.add_to(clusters_center)
    elif df_perispiiri.index[i] in ["401","402","403","404","405"]:
        markers.add_to(clusters_north)
    elif df_perispiiri.index[i] in ["501","502","503","504","505","506"]:
        markers.add_to(clusters_koillinen)
    elif df_perispiiri.index[i] in ["601","602","603"]:
        markers.add_to(clusters_kaakkoinen)
    elif df_perispiiri.index[i] in ["701","702","703","704"]:
        markers.add_to(clusters_east)
    elif df_perispiiri.index[i] in ["801"]:
        markers.add_to(clusters_oster)
    #catch
    else:
        markers.add_to(clusters_south)

diff = curr_year - 1985

#population markers
for j in range(num_years):

    for i in range(num_1):
        if df_perispiiri_pop.iloc[i,j] != 0:
            pop_curr = df_perispiiri_pop.iloc[i,j] 
            radius = pop_curr /1000

            if j >0:
                delta = pop_curr - df_perispiiri_pop.iloc[i,j-1]
                if delta > 0:
                    delta_change = 1
                else:
                    delta_change = 0
            else: 
                delta_change = 1 

            if delta_change == 0:
                colour = "red"
            else:
                colour = "blue"
            dat1 = "<b>Change from previous year:</b>" + str(delta_change)

            iframe = folium.IFrame(html=dat1, width=200, height=60)
            popup = folium.Popup(iframe, max_width=2650)
    
            circles = folium.CircleMarker(location=df_perispiiri.coordinates.iloc[i],
                                radius = radius,
                                color=colour,
                                tooltip = '<b>Population in {}: {}</b>'.format( j+1985,pop_curr.astype(int)),
                                fill = True,
                                popup = popup,
                                #(True if np.abs(diff - j) == 0 else False),
                                opacity = (1 if np.abs(diff - j) == 0 else 0.1),
                                )
            
            if df_perispiiri.index[i] in ["101","102","103","104","105"]:
                circles.add_to(clusters_south)
            elif df_perispiiri.index[i] in ["201","202","203","204","205"]:
                circles.add_to(clusters_west)
            elif df_perispiiri.index[i] in ["301}","302","303","304","305"]:
                circles.add_to(clusters_center)
            elif df_perispiiri.index[i] in ["401","402","403","404","405"]:
                circles.add_to(clusters_north)
            elif df_perispiiri.index[i] in ["501","502","503","504","505","506"]:
                circles.add_to(clusters_koillinen)
            elif df_perispiiri.index[i] in ["601","602","603"]:
                circles.add_to(clusters_kaakkoinen)
            elif df_perispiiri.index[i] in ["701","702","703","704"]:
                circles.add_to(clusters_east)
            elif df_perispiiri.index[i] in ["801"]:
                circles.add_to(clusters_oster)
            #catch if errors
            else:
                circles.add_to(clusters_south)

#cluster into spiral
clusters_dists = plugins.MarkerCluster(overlay=True, 
                    icon_create_function = icon_create_function,
                    control=True,
                    show=True
                    )
clusters_dists.add_to(fg_dists)



#for large districts
for i in range(len(df_suuri_pop.index)):
    pop_loc = curr_year - 1985
    pop_curr = df_suuri_pop.iloc[i,pop_loc] 
    
    dat1 = '<b>Population in </b>' + str(curr_year) + ": " + str(pop_curr.astype(int))

    iframe = folium.IFrame(html=dat1, width=200, height=60)
    popup = folium.Popup(iframe, max_width=2650)
    
    markers = folium.Marker(
        location=df_suuri.coordinates.iloc[i], # coordinates for the marker
        icon=folium.Icon(icon = "info-sign",
                        icon_color = "white"),
        popup = popup,
        #add place name as tool tip on hover
        tooltip = df_suuri.District.iloc[i],
        )
    
    markers.add_to(fg_dists)

folium.LayerControl(position="topright",
                    autoZIndex = True, 
                    collapsed = False).add_to(map_1)

In [ ]:

map_1

In [ ]:
map_1.save("test.html")

#uncomment to download
#files.download('test.html')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>